In [1]:
import localprojections as lp

# If this doesn't work, install the package: pip install localprojections

In [3]:
# To understand documentation
help(lp.PanelLP)

Help on function PanelLP in module localprojections.lp:

PanelLP(data, Y, response, horizon, lags, varcov='kernel', ci_width=0.95)
    ### PanelLP
    ## Input attributes
    # data = pandas entity-time(int64 or datetime) multi-indexed dataframe
    # Y = list of variables, cholesky ordered (last = contemporaneous shock from all previous variables)
    # response = list of variables contained in Y to be shocked
    # horizon = integer indicating estimation horizon for the IRFs (e.g., input 8 for 8 quarters ahead)
    # lags = integer indicating number of lags to be used in the estimation models (e.g., 4 for 4 lags)
    # varcov = string indicating type of varcov, see PanelOLS documentation
    # ci_width = float within (0, 1) indicating the width of the confidence band (e.g., 0.95 for 95% CI)



This function returns a pandas dataframe of 6 columns:

1. Shock indicates the shock variable
2. Response indicates the response variable
3. Horizon indicates the response horizon of the IRF
4. Mean indicates the point estimate of the IRF
5. LB indicates the lower bound of the confidence interval of the IRF
6. LB indicates the upper bound of the confidence interval of the IRF

For instance, the estimates of the 6-period ahead IRF of y from a shock in x, can be found in the row with Shock=x, Response=y, and Horizon=6

In [4]:
# Example
from statsmodels.datasets import grunfeld

In [7]:
df = grunfeld.load_pandas().data # import the Grunfeld investment data set
df = df.set_index(['firm', 'year']) # set entity-year indices (as per requirements in bashtage's linearmodels)

endog = ['invest', 'value', 'capital'] # cholesky ordering: invest --> value --> capital
response = endog.copy() # estimate the responses of all variables to shocks from all variables
irf_horizon = 8 # estimate IRFs up to 8 periods ahead
opt_lags = 2 # include 2 lags in the local projections model
opt_cov = 'robust' # HAC standard errors
opt_ci = 0.95 # 95% confidence intervals

In [8]:
irf = lp.PanelLP(data=df, # input dataframe
                 Y=endog, # variables in the model
                 response=response, # variables whose IRFs should be estimated
                 horizon=irf_horizon, # estimation horizon of IRFs
                 lags=opt_lags, # lags in the model
                 varcov=opt_cov, # type of standard errors
                 ci_width=opt_ci # width of confidence band
                 )

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:87: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  irf_full = pd.concat([irf_full, irf], axis=0) # top to bottom concat


In [9]:
irfplot = lp.IRFPlot(irf=irf, # take output from the estimated model
                     response=['invest'], # plot only response of invest ...
                     shock=endog, # ... to shocks from all variables
                     n_columns=2, # max 2 columns in the figure
                     n_rows=2, # max 2 rows in the figure
                     maintitle='Panel LP: IRFs of Investment', # self-defined title of the IRF plot
                     show_fig=True, # display figure (from plotly)
                     save_pic=False # don't save any figures on local drive
                     )

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:212: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:212: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:212: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pyda

## Time Series Local Projections

In [10]:
help(lp.TimeSeriesLP)

Help on function TimeSeriesLP in module localprojections.lp:

TimeSeriesLP(data, Y, response, horizon, lags, newey_lags=4, ci_width=0.95)
    ### TimeSeriesLP
    ## Input attributes
    # This is almost identical procedurally with the Panel version
    # data = pandas dataframe (each row = 1 period)
    # Y = list of variables, cholesky ordered (last = contemporaneous shock from all previous variables)
    # response = list of variables contained in Y to be shocked
    # horizon = integer indicating estimation horizon for the IRFs (e.g., input 8 for 8 quarters ahead)
    # lags = integer indicating number of lags to be used in the estimation models (e.g., 4 for 4 lags)
    # newey_lags = max lags for Newey-West HAC SEs
    # ci_width = float within (0, 1) indicating the width of the confidence band (e.g., 0.95 for 95% CI)



In [11]:
df = grunfeld.load_pandas().data # import the Grunfeld investment data set
df = df[df['firm'] == 'General Motors'] # keep only one entity (as an example of a single entity time series setting)
df = df.set_index(['year']) # set time variable as index

endog = ['invest', 'value', 'capital'] # cholesky ordering: invest --> value --> capital
response = endog.copy() # estimate the responses of all variables to shocks from all variables
irf_horizon = 8 # estimate IRFs up to 8 periods ahead
opt_lags = 2 # include 2 lags in the local projections model
opt_cov = 'robust' # HAC standard errors
opt_ci = 0.95 # 95% confidence intervals

# Use TimeSeriesLP for the single entity case
irf = lp.TimeSeriesLP(data=df, # input dataframe
                      Y=endog, # variables in the model
                      response=response, # variables whose IRFs should be estimated
                      horizon=irf_horizon, # estimation horizon of IRFs
                      lags=opt_lags, # lags in the model
                      newey_lags=2, # maximum lags when estimating Newey-West standard errors
                      ci_width=opt_ci # width of confidence band
                      )
irfplot = lp.IRFPlot(irf=irf, # take output from the estimated model
                     response=['invest'], # plot only response of invest ...
                     shock=endog, # ... to shocks from all variables
                     n_columns=2, # max 2 columns in the figure
                     n_rows=2, # max 2 rows in the figure
                     maintitle='Single Entity Time Series LP: IRFs of Investment', # self-defined title of the IRF plot
                     show_fig=True, # display figure (from plotly)
                     save_pic=False # don't save any figures on local drive
                     )

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:166: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:212: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\valte\anaconda3\lib\site-packages\localprojections\lp.py:212: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://panda